# 0. Preparation

In [0]:
from pyspark.sql.functions import *
from delta import DeltaTable
from datetime import datetime
from delta.tables import DeltaTable

In [0]:
# define data paths
username = "ran_wei"

moviePipelinePath = f"/antraBI/{username}/movie/Pipline/"

landingPath = moviePipelinePath + "landing/"
rawPath = moviePipelinePath + "raw/"
bronzePath = moviePipelinePath + "bronze/"
movieSilverPath = moviePipelinePath + "silver/Movie/"
genreSilverPath = moviePipelinePath + "silver/Genre/"
olSilverPath = moviePipelinePath + "silver/OriginalLanguages/"
movieSilverUpdatePath = moviePipelinePath + "silverUpdate/Movie"

In [0]:
# set raw data source
raw_directory = 'dbfs:/FileStore/movie_source/*.json'

In [0]:
# make notebook idempotent
dbutils.fs.rm(moviePipelinePath, recurse=True)

True

# 1. Display Raw Data

In [0]:
# display raw data
rawDF = (spark.read
         .option("multiline", "true")
         .format("json")
         .load(raw_directory)
         .select(explode("movie").alias("movies")))

In [0]:
display(rawDF.limit(5))

movies List(https://image.tmdb.org/t/p/original//s3TBrRGB1iav7gFOCNx3H31MoES.jpg, 1.6E8, null, 2021-04-03T16:51:30.1633333, 1, https://www.imdb.com/title/tt1375666, en, Cobb, a skilled thief who commits corporate espionage by infiltrating the subconscious of his targets is offered a chance to regain his old life as payment for a task considered to be impossible: "inception", the implantation of another person's idea into a target's subconscious., https://image.tmdb.org/t/p/w342//9gk7adHYeDvHkCSEqAvQNLV5Uge.jpg, 9.9, 2010-07-15T00:00:00, 8.25532764E8, 148, Your mind is the scene of the crime., Inception, https://www.themoviedb.org/movie/27205, null, null, List(List(1, Adventure), List(6, Action), List(13, Science Fiction))) List(https://image.tmdb.org/t/p/original//xJHokMbljvjADYdit5fK5VQsXEG.jpg, 1.65E8, null, 2021-04-03T16:51:30.1633333, 2, https://www.imdb.com/title/tt0816692, en, The adventures of a group of explorers who make use of a newly discovered wormhole to surpass the limitations on human space travel and conquer the vast distances involved in an interstellar voyage., https://image.tmdb.org/t/p/w342//gEU2QniE6E77NI6lCU6MxlNBvIx.jpg, 9.9, 2014-11-05T00:00:00, 6.75120017E8, 169, Mankind was born on Earth. It was never meant to die here., Interstellar, https://www.themoviedb.org/movie/157336, null, null, List(List(1, Adventure), List(4, Drama), List(13, Science Fiction))) List(https://image.tmdb.org/t/p/original//hkBaDkMWbLaf8B1lsWsKX7Ew3Xq.jpg, 1.85E8, null, 2021-04-03T16:51:30.1633333, 3, https://www.imdb.com/title/tt0468569, en, Batman raises the stakes in his war on crime. With the help of Lt. Jim Gordon and District Attorney Harvey Dent, Batman sets out to dismantle the remaining criminal organizations that plague the streets. The partnership proves to be effective, but they soon find themselves prey to a reign of chaos unleashed by a rising criminal mastermind known to the terrified citizens of Gotham as the Joker., https://image.tmdb.org/t/p/w342//qJ2tW6WMUDux911r6m7haRef0WH.jpg, 9.9, 2008-07-16T00:00:00, 1.004558444E9, 152, Why So Serious?, The Dark Knight, https://www.themoviedb.org/movie/155, null, null, List(List(4, Drama), List(6, Action), List(10, Thriller), List(11, Crime))) List(https://image.tmdb.org/t/p/original//en971MEXui9diirXlogOrPKmsEn.jpg, 5.8E7, null, 2021-04-03T16:51:30.1633333, 4, https://www.imdb.com/title/tt1431045, en, Deadpool tells the origin story of former Special Forces operative turned mercenary Wade Wilson, who after being subjected to a rogue experiment that leaves him with accelerated healing powers, adopts the alter ego Deadpool. Armed with his new abilities and a dark, twisted sense of humor, Deadpool hunts down the man who nearly destroyed his life., https://image.tmdb.org/t/p/w342//yGSxMiF0cYuAiyuve5DA6bnWEOI.jpg, 9.9, 2016-02-09T00:00:00, 7.831E8, 108, Witness the beginning of a happy ending, Deadpool, https://www.themoviedb.org/movie/293660, null, null, List(List(1, Adventure), List(6, Action), List(7, Comedy))) List(https://image.tmdb.org/t/p/original//kwUQFeFXOOpgloMgZaadhzkbTI4.jpg, 2.2E8, null, 2021-04-03T16:51:30.1666667, 5, https://www.imdb.com/title/tt0848228, en, When an unexpected enemy emerges and threatens global safety and security, Nick Fury, director of the international peacekeeping agency known as S.H.I.E.L.D., finds himself in need of a team to pull the world back from the brink of disaster. Spanning the globe, a daring recruitment effort begins!, https://image.tmdb.org/t/p/w342//RYMX2wcKCBAr24UyPD7xwmjaTn.jpg, 9.9, 2012-04-25T00:00:00, 1.51955791E9, 143, Some assembly required., The Avengers, https://www.themoviedb.org/movie/24428, null, null, List(List(1, Adventure), List(6, Action), List(13, Science Fiction)))

In [0]:
(
    rawDF.select(
        "movies"
    )
    .write.format("delta")
    .mode("overwrite")
    .save(rawPath)
)

In [0]:
display(dbutils.fs.ls(rawPath))

path name size modificationTime dbfs:/antraBI/ran_wei/movie/Pipline/raw/_delta_log/ _delta_log/ 0 1691348084000 dbfs:/antraBI/ran_wei/movie/Pipline/raw/part-00000-96a134be-49ed-4c80-9172-87d0bf930d46-c000.snappy.parquet part-00000-96a134be-49ed-4c80-9172-87d0bf930d46-c000.snappy.parquet 847064 1691348085000 dbfs:/antraBI/ran_wei/movie/Pipline/raw/part-00001-ad1bfef9-bbde-48db-82b6-6af56b0d9467-c000.snappy.parquet part-00001-ad1bfef9-bbde-48db-82b6-6af56b0d9467-c000.snappy.parquet 827311 1691348085000 dbfs:/antraBI/ran_wei/movie/Pipline/raw/part-00002-66f26539-b515-47f7-a43c-2aa46152cfd6-c000.snappy.parquet part-00002-66f26539-b515-47f7-a43c-2aa46152cfd6-c000.snappy.parquet 825951 1691348085000 dbfs:/antraBI/ran_wei/movie/Pipline/raw/part-00003-e386bac9-79ab-44a7-9dc9-682222295175-c000.snappy.parquet part-00003-e386bac9-79ab-44a7-9dc9-682222295175-c000.snappy.parquet 827883 1691348085000

# 2. Raw to Bronze

##2.1 Ingest Metadata

In [0]:
bronzeDF = rawDF.select(
    "movies",
    lit('dbfs:/FileStore/movie_source/*.json').alias("datasource"),
    current_timestamp().alias("ingesttime"),
    lit("new").alias("status"),
    current_timestamp().cast("date").alias("ingestdate"),
)

In [0]:
display(bronzeDF.limit(5))

movies datasource ingesttime status ingestdate List(https://image.tmdb.org/t/p/original//s3TBrRGB1iav7gFOCNx3H31MoES.jpg, 1.6E8, null, 2021-04-03T16:51:30.1633333, 1, https://www.imdb.com/title/tt1375666, en, Cobb, a skilled thief who commits corporate espionage by infiltrating the subconscious of his targets is offered a chance to regain his old life as payment for a task considered to be impossible: "inception", the implantation of another person's idea into a target's subconscious., https://image.tmdb.org/t/p/w342//9gk7adHYeDvHkCSEqAvQNLV5Uge.jpg, 9.9, 2010-07-15T00:00:00, 8.25532764E8, 148, Your mind is the scene of the crime., Inception, https://www.themoviedb.org/movie/27205, null, null, List(List(1, Adventure), List(6, Action), List(13, Science Fiction))) dbfs:/FileStore/movie_source/*.json 2023-08-06T18:55:01.939+0000 new 2023-08-06 List(https://image.tmdb.org/t/p/original//xJHokMbljvjADYdit5fK5VQsXEG.jpg, 1.65E8, null, 2021-04-03T16:51:30.1633333, 2, https://www.imdb.com/title/tt0816692, en, The adventures of a group of explorers who make use of a newly discovered wormhole to surpass the limitations on human space travel and conquer the vast distances involved in an interstellar voyage., https://image.tmdb.org/t/p/w342//gEU2QniE6E77NI6lCU6MxlNBvIx.jpg, 9.9, 2014-11-05T00:00:00, 6.75120017E8, 169, Mankind was born on Earth. It was never meant to die here., Interstellar, https://www.themoviedb.org/movie/157336, null, null, List(List(1, Adventure), List(4, Drama), List(13, Science Fiction))) dbfs:/FileStore/movie_source/*.json 2023-08-06T18:55:01.939+0000 new 2023-08-06 List(https://image.tmdb.org/t/p/original//hkBaDkMWbLaf8B1lsWsKX7Ew3Xq.jpg, 1.85E8, null, 2021-04-03T16:51:30.1633333, 3, https://www.imdb.com/title/tt0468569, en, Batman raises the stakes in his war on crime. With the help of Lt. Jim Gordon and District Attorney Harvey Dent, Batman sets out to dismantle the remaining criminal organizations that plague the streets. The partnership proves to be effective, but they soon find themselves prey to a reign of chaos unleashed by a rising criminal mastermind known to the terrified citizens of Gotham as the Joker., https://image.tmdb.org/t/p/w342//qJ2tW6WMUDux911r6m7haRef0WH.jpg, 9.9, 2008-07-16T00:00:00, 1.004558444E9, 152, Why So Serious?, The Dark Knight, https://www.themoviedb.org/movie/155, null, null, List(List(4, Drama), List(6, Action), List(10, Thriller), List(11, Crime))) dbfs:/FileStore/movie_source/*.json 2023-08-06T18:55:01.939+0000 new 2023-08-06 List(https://image.tmdb.org/t/p/original//en971MEXui9diirXlogOrPKmsEn.jpg, 5.8E7, null, 2021-04-03T16:51:30.1633333, 4, https://www.imdb.com/title/tt1431045, en, Deadpool tells the origin story of former Special Forces operative turned mercenary Wade Wilson, who after being subjected to a rogue experiment that leaves him with accelerated healing powers, adopts the alter ego Deadpool. Armed with his new abilities and a dark, twisted sense of humor, Deadpool hunts down the man who nearly destroyed his life., https://image.tmdb.org/t/p/w342//yGSxMiF0cYuAiyuve5DA6bnWEOI.jpg, 9.9, 2016-02-09T00:00:00, 7.831E8, 108, Witness the beginning of a happy ending, Deadpool, https://www.themoviedb.org/movie/293660, null, null, List(List(1, Adventure), List(6, Action), List(7, Comedy))) dbfs:/FileStore/movie_source/*.json 2023-08-06T18:55:01.939+0000 new 2023-08-06 List(https://image.tmdb.org/t/p/original//kwUQFeFXOOpgloMgZaadhzkbTI4.jpg, 2.2E8, null, 2021-04-03T16:51:30.1666667, 5, https://www.imdb.com/title/tt0848228, en, When an unexpected enemy emerges and threatens global safety and security, Nick Fury, director of the international peacekeeping agency known as S.H.I.E.L.D., finds himself in need of a team to pull the world back from the brink of disaster. Spanning the globe, a daring recruitment effort begins!, https://image.tmdb.org/t/p/w342//RYMX2wcKCBAr24UyPD7xwmjaTn.jpg, 9.9, 2012-04-25T00:00:00, 1.51955791E9, 143, Some assembly required., The Avengers, https://www.

##2.2 WRITE Batch to a Bronze Table

In [0]:
(
    bronzeDF.select(
        "datasource",
        "ingesttime",
        "movies",
        "status",
        col("ingestdate").alias("p_ingestdate"),
    )
    .write.format("delta")
    .mode("overwrite")
    .partitionBy("p_ingestdate")
    .save(bronzePath)
)

In [0]:
display(dbutils.fs.ls(bronzePath))

path name size modificationTime dbfs:/antraBI/ran_wei/movie/Pipline/bronze/_delta_log/ _delta_log/ 0 1691348107000 dbfs:/antraBI/ran_wei/movie/Pipline/bronze/p_ingestdate=2023-08-06/ p_ingestdate=2023-08-06/ 0 1691348107000

##2.3 Register the Bronze Table in the Metastore

In [0]:
spark.sql(f"""DROP TABLE IF EXISTS movie_bronze""")

DataFrame[]

In [0]:
spark.sql(
    f"""
    CREATE TABLE movie_bronze
    USING DELTA
    LOCATION "{bronzePath}"
    """
)

DataFrame[]

In [0]:
bronzeDF = spark.read.table("movie_bronze")

In [0]:
display(bronzeDF.limit(5))

datasource ingesttime movies status p_ingestdate dbfs:/FileStore/movie_source/*.json 2023-08-06T18:55:07.273+0000 List(https://image.tmdb.org/t/p/original//s3TBrRGB1iav7gFOCNx3H31MoES.jpg, 1.6E8, null, 2021-04-03T16:51:30.1633333, 1, https://www.imdb.com/title/tt1375666, en, Cobb, a skilled thief who commits corporate espionage by infiltrating the subconscious of his targets is offered a chance to regain his old life as payment for a task considered to be impossible: "inception", the implantation of another person's idea into a target's subconscious., https://image.tmdb.org/t/p/w342//9gk7adHYeDvHkCSEqAvQNLV5Uge.jpg, 9.9, 2010-07-15T00:00:00, 8.25532764E8, 148, Your mind is the scene of the crime., Inception, https://www.themoviedb.org/movie/27205, null, null, List(List(1, Adventure), List(6, Action), List(13, Science Fiction))) new 2023-08-06 dbfs:/FileStore/movie_source/*.json 2023-08-06T18:55:07.273+0000 List(https://image.tmdb.org/t/p/original//xJHokMbljvjADYdit5fK5VQsXEG.jpg, 1.65E8, null, 2021-04-03T16:51:30.1633333, 2, https://www.imdb.com/title/tt0816692, en, The adventures of a group of explorers who make use of a newly discovered wormhole to surpass the limitations on human space travel and conquer the vast distances involved in an interstellar voyage., https://image.tmdb.org/t/p/w342//gEU2QniE6E77NI6lCU6MxlNBvIx.jpg, 9.9, 2014-11-05T00:00:00, 6.75120017E8, 169, Mankind was born on Earth. It was never meant to die here., Interstellar, https://www.themoviedb.org/movie/157336, null, null, List(List(1, Adventure), List(4, Drama), List(13, Science Fiction))) new 2023-08-06 dbfs:/FileStore/movie_source/*.json 2023-08-06T18:55:07.273+0000 List(https://image.tmdb.org/t/p/original//hkBaDkMWbLaf8B1lsWsKX7Ew3Xq.jpg, 1.85E8, null, 2021-04-03T16:51:30.1633333, 3, https://www.imdb.com/title/tt0468569, en, Batman raises the stakes in his war on crime. With the help of Lt. Jim Gordon and District Attorney Harvey Dent, Batman sets out to dismantle the remaining criminal organizations that plague the streets. The partnership proves to be effective, but they soon find themselves prey to a reign of chaos unleashed by a rising criminal mastermind known to the terrified citizens of Gotham as the Joker., https://image.tmdb.org/t/p/w342//qJ2tW6WMUDux911r6m7haRef0WH.jpg, 9.9, 2008-07-16T00:00:00, 1.004558444E9, 152, Why So Serious?, The Dark Knight, https://www.themoviedb.org/movie/155, null, null, List(List(4, Drama), List(6, Action), List(10, Thriller), List(11, Crime))) new 2023-08-06 dbfs:/FileStore/movie_source/*.json 2023-08-06T18:55:07.273+0000 List(https://image.tmdb.org/t/p/original//en971MEXui9diirXlogOrPKmsEn.jpg, 5.8E7, null, 2021-04-03T16:51:30.1633333, 4, https://www.imdb.com/title/tt1431045, en, Deadpool tells the origin story of former Special Forces operative turned mercenary Wade Wilson, who after being subjected to a rogue experiment that leaves him with accelerated healing powers, adopts the alter ego Deadpool. Armed with his new abilities and a dark, twisted sense of humor, Deadpool hunts down the man who nearly destroyed his life., https://image.tmdb.org/t/p/w342//yGSxMiF0cYuAiyuve5DA6bnWEOI.jpg, 9.9, 2016-02-09T00:00:00, 7.831E8, 108, Witness the beginning of a happy ending, Deadpool, https://www.themoviedb.org/movie/293660, null, null, List(List(1, Adventure), List(6, Action), List(7, Comedy))) new 2023-08-06 dbfs:/FileStore/movie_source/*.json 2023-08-06T18:55:07.273+0000 List(https://image.tmdb.org/t/p/original//kwUQFeFXOOpgloMgZaadhzkbTI4.jpg, 2.2E8, null, 2021-04-03T16:51:30.1666667, 5, https://www.imdb.com/title/tt0848228, en, When an unexpected enemy emerges and threatens global safety and security, Nick Fury, director of the international peacekeeping agency known as S.H.I.E.L.D., finds himself in need of a team to pull the world back from the brink of disaster. Spanning the globe, a daring recruitment effort begins!, https://image.tmdb.org/t/p/w342//RYMX2wcKCBAr24UyPD7xwmjaTn.jpg, 9.9, 2012-04-25T00:00:00, 1.5

# 3. Bronze to Silver

In [0]:
# add a widget to specify what data to load from bronze based on the “ingest_date”
date_list = spark.sql("select distinct(date(ingesttime)) from movie_bronze").collect()
print(date_list)

[Row(ingesttime=datetime.date(2023, 8, 6))]


In [0]:
dbutils.widgets.dropdown("date","2023-08-06",[row[0].strftime("%Y-%m-%d") for row in date_list])

In [0]:
bronzeDF=bronzeDF.filter(date_format("ingesttime","yyyy-MM-dd") == getArgument("date"))

In [0]:
display(bronzeDF.limit(5))

datasource ingesttime movies status p_ingestdate dbfs:/FileStore/movie_source/*.json 2023-08-06T18:55:07.273+0000 List(https://image.tmdb.org/t/p/original//s3TBrRGB1iav7gFOCNx3H31MoES.jpg, 1.6E8, null, 2021-04-03T16:51:30.1633333, 1, https://www.imdb.com/title/tt1375666, en, Cobb, a skilled thief who commits corporate espionage by infiltrating the subconscious of his targets is offered a chance to regain his old life as payment for a task considered to be impossible: "inception", the implantation of another person's idea into a target's subconscious., https://image.tmdb.org/t/p/w342//9gk7adHYeDvHkCSEqAvQNLV5Uge.jpg, 9.9, 2010-07-15T00:00:00, 8.25532764E8, 148, Your mind is the scene of the crime., Inception, https://www.themoviedb.org/movie/27205, null, null, List(List(1, Adventure), List(6, Action), List(13, Science Fiction))) new 2023-08-06 dbfs:/FileStore/movie_source/*.json 2023-08-06T18:55:07.273+0000 List(https://image.tmdb.org/t/p/original//xJHokMbljvjADYdit5fK5VQsXEG.jpg, 1.65E8, null, 2021-04-03T16:51:30.1633333, 2, https://www.imdb.com/title/tt0816692, en, The adventures of a group of explorers who make use of a newly discovered wormhole to surpass the limitations on human space travel and conquer the vast distances involved in an interstellar voyage., https://image.tmdb.org/t/p/w342//gEU2QniE6E77NI6lCU6MxlNBvIx.jpg, 9.9, 2014-11-05T00:00:00, 6.75120017E8, 169, Mankind was born on Earth. It was never meant to die here., Interstellar, https://www.themoviedb.org/movie/157336, null, null, List(List(1, Adventure), List(4, Drama), List(13, Science Fiction))) new 2023-08-06 dbfs:/FileStore/movie_source/*.json 2023-08-06T18:55:07.273+0000 List(https://image.tmdb.org/t/p/original//hkBaDkMWbLaf8B1lsWsKX7Ew3Xq.jpg, 1.85E8, null, 2021-04-03T16:51:30.1633333, 3, https://www.imdb.com/title/tt0468569, en, Batman raises the stakes in his war on crime. With the help of Lt. Jim Gordon and District Attorney Harvey Dent, Batman sets out to dismantle the remaining criminal organizations that plague the streets. The partnership proves to be effective, but they soon find themselves prey to a reign of chaos unleashed by a rising criminal mastermind known to the terrified citizens of Gotham as the Joker., https://image.tmdb.org/t/p/w342//qJ2tW6WMUDux911r6m7haRef0WH.jpg, 9.9, 2008-07-16T00:00:00, 1.004558444E9, 152, Why So Serious?, The Dark Knight, https://www.themoviedb.org/movie/155, null, null, List(List(4, Drama), List(6, Action), List(10, Thriller), List(11, Crime))) new 2023-08-06 dbfs:/FileStore/movie_source/*.json 2023-08-06T18:55:07.273+0000 List(https://image.tmdb.org/t/p/original//en971MEXui9diirXlogOrPKmsEn.jpg, 5.8E7, null, 2021-04-03T16:51:30.1633333, 4, https://www.imdb.com/title/tt1431045, en, Deadpool tells the origin story of former Special Forces operative turned mercenary Wade Wilson, who after being subjected to a rogue experiment that leaves him with accelerated healing powers, adopts the alter ego Deadpool. Armed with his new abilities and a dark, twisted sense of humor, Deadpool hunts down the man who nearly destroyed his life., https://image.tmdb.org/t/p/w342//yGSxMiF0cYuAiyuve5DA6bnWEOI.jpg, 9.9, 2016-02-09T00:00:00, 7.831E8, 108, Witness the beginning of a happy ending, Deadpool, https://www.themoviedb.org/movie/293660, null, null, List(List(1, Adventure), List(6, Action), List(7, Comedy))) new 2023-08-06 dbfs:/FileStore/movie_source/*.json 2023-08-06T18:55:07.273+0000 List(https://image.tmdb.org/t/p/original//kwUQFeFXOOpgloMgZaadhzkbTI4.jpg, 2.2E8, null, 2021-04-03T16:51:30.1666667, 5, https://www.imdb.com/title/tt0848228, en, When an unexpected enemy emerges and threatens global safety and security, Nick Fury, director of the international peacekeeping agency known as S.H.I.E.L.D., finds himself in need of a team to pull the world back from the brink of disaster. Spanning the globe, a daring recruitment effort begins!, https://image.tmdb.org/t/p/w342//RYMX2wcKCBAr24UyPD7xwmjaTn.jpg, 9.9, 2012-04-25T00:00:00, 1.5

##3.1 Movie Table

In [0]:
# Extract the Nested JSON from the Bronze Records
movieBronzeAugmentedDF = bronzeDF.select(
                                          "movies.Id",
                                          "movies.Title",
                                          "movies.Overview",
                                          "movies.Tagline",
                                          "movies.RunTime",
                                          "movies.Price",
                                          "movies.Budget",
                                          "movies.Revenue",
                                          "movies.CreatedBy",
                                          "movies.CreatedDate",
                                          "movies.ReleaseDate",
                                          "movies.UpdatedBy",
                                          "movies.UpdatedDate",
                                          "movies.BackdropUrl",
                                          "movies.ImdbUrl",
                                          "movies.PosterUrl",
                                          "movies.TmdbUrl",
                                          "movies"
                                        )

In [0]:
# Create the Silver DataFrame
movieSilverDF = movieBronzeAugmentedDF.select(
                                              col("Id").alias("Movie_id"),
                                              col("Title"),
                                              col("Overview"),
                                              col("Tagline"),
                                              col("RunTime"),
                                              col("Price"),
                                              col("Budget"),
                                              col("Revenue"),
                                              col("CreatedBy"),
                                              col("CreatedDate"),
                                              col("ReleaseDate"),
                                              col("UpdatedBy"),
                                              col("UpdatedDate"),
                                              col("BackdropUrl"),
                                              col("ImdbUrl"),
                                              col("PosterUrl"),
                                              col("TmdbUrl"),
                                              "movies"
                                              )

In [0]:
display(movieSilverDF.limit(5))

Movie_id Title Overview Tagline RunTime Price Budget Revenue CreatedBy CreatedDate ReleaseDate UpdatedBy UpdatedDate BackdropUrl ImdbUrl PosterUrl TmdbUrl movies 1 Inception Cobb, a skilled thief who commits corporate espionage by infiltrating the subconscious of his targets is offered a chance to regain his old life as payment for a task considered to be impossible: "inception", the implantation of another person's idea into a target's subconscious. Your mind is the scene of the crime. 148 9.9 1.6E8 8.25532764E8 null 2021-04-03T16:51:30.1633333 2010-07-15T00:00:00 null null https://image.tmdb.org/t/p/original//s3TBrRGB1iav7gFOCNx3H31MoES.jpg https://www.imdb.com/title/tt1375666 https://image.tmdb.org/t/p/w342//9gk7adHYeDvHkCSEqAvQNLV5Uge.jpg https://www.themoviedb.org/movie/27205 List(https://image.tmdb.org/t/p/original//s3TBrRGB1iav7gFOCNx3H31MoES.jpg, 1.6E8, null, 2021-04-03T16:51:30.1633333, 1, https://www.imdb.com/title/tt1375666, en, Cobb, a skilled thief who commits corporate espionage by infiltrating the subconscious of his targets is offered a chance to regain his old life as payment for a task considered to be impossible: "inception", the implantation of another person's idea into a target's subconscious., https://image.tmdb.org/t/p/w342//9gk7adHYeDvHkCSEqAvQNLV5Uge.jpg, 9.9, 2010-07-15T00:00:00, 8.25532764E8, 148, Your mind is the scene of the crime., Inception, https://www.themoviedb.org/movie/27205, null, null, List(List(1, Adventure), List(6, Action), List(13, Science Fiction))) 2 Interstellar The adventures of a group of explorers who make use of a newly discovered wormhole to surpass the limitations on human space travel and conquer the vast distances involved in an interstellar voyage. Mankind was born on Earth. It was never meant to die here. 169 9.9 1.65E8 6.75120017E8 null 2021-04-03T16:51:30.1633333 2014-11-05T00:00:00 null null https://image.tmdb.org/t/p/original//xJHokMbljvjADYdit5fK5VQsXEG.jpg https://www.imdb.com/title/tt0816692 https://image.tmdb.org/t/p/w342//gEU2QniE6E77NI6lCU6MxlNBvIx.jpg https://www.themoviedb.org/movie/157336 List(https://image.tmdb.org/t/p/original//xJHokMbljvjADYdit5fK5VQsXEG.jpg, 1.65E8, null, 2021-04-03T16:51:30.1633333, 2, https://www.imdb.com/title/tt0816692, en, The adventures of a group of explorers who make use of a newly discovered wormhole to surpass the limitations on human space travel and conquer the vast distances involved in an interstellar voyage., https://image.tmdb.org/t/p/w342//gEU2QniE6E77NI6lCU6MxlNBvIx.jpg, 9.9, 2014-11-05T00:00:00, 6.75120017E8, 169, Mankind was born on Earth. It was never meant to die here., Interstellar, https://www.themoviedb.org/movie/157336, null, null, List(List(1, Adventure), List(4, Drama), List(13, Science Fiction))) 3 The Dark Knight Batman raises the stakes in his war on crime. With the help of Lt. Jim Gordon and District Attorney Harvey Dent, Batman sets out to dismantle the remaining criminal organizations that plague the streets. The partnership proves to be effective, but they soon find themselves prey to a reign of chaos unleashed by a rising criminal mastermind known to the terrified citizens of Gotham as the Joker. Why So Serious? 152 9.9 1.85E8 1.004558444E9 null 2021-04-03T16:51:30.1633333 2008-07-16T00:00:00 null null https://image.tmdb.org/t/p/original//hkBaDkMWbLaf8B1lsWsKX7Ew3Xq.jpg https://www.imdb.com/title/tt0468569 https://image.tmdb.org/t/p/w342//qJ2tW6WMUDux911r6m7haRef0WH.jpg https://www.themoviedb.org/movie/155 List(https://image.tmdb.org/t/p/original//hkBaDkMWbLaf8B1lsWsKX7Ew3Xq.jpg, 1.85E8, null, 2021-04-03T16:51:30.1633333, 3, https://www.imdb.com/title/tt0468569, en, Batman raises the stakes in his war on crime. With the help of Lt. Jim Gordon and District Attorney Harvey Dent, Batman sets out to dismantle the remaining criminal organizations that plague the streets. The partnership proves to be effective, but they soon find themselves prey to a reign of chaos unleashed by a rising criminal mastermind kn

In [0]:
# Quarantine the Bad Data
movieSilverDF.count()

9995

In [0]:
## filter the records with negative RunTime
display(movieSilverDF.filter("RunTime < 0"))

Movie_id Title Overview Tagline RunTime Price Budget Revenue CreatedBy CreatedDate ReleaseDate UpdatedBy UpdatedDate BackdropUrl ImdbUrl PosterUrl TmdbUrl movies

There's no movie have a negative runtime.

In [0]:
## filter the records with budget<1 million
movieSilverDF.filter("Budget < 1000000").count()

4480

In [0]:
## filter the records with same movie_id
duplicateCounts = movieSilverDF.groupBy("Movie_id").count().orderBy(desc("count"))
display(duplicateCounts.limit(5))

Movie_id count 26 1 29 1 474 1 964 1 1677 1

No duplicates in movie_id. But if there exists duplicates, we should also mark the same movie_id as 'quarantined' then decide wether to fix it when updating silver table.

In [0]:
movieSilverDF_clean = movieSilverDF.filter("budget >= 1000000")
movieSilverDF_quarantine = movieSilverDF.filter("budget < 1000000")

In [0]:
print(movieSilverDF_clean.count())
print(movieSilverDF_quarantine.count())
print(movieSilverDF.count())

5515
4480
9995


In [0]:
# WRITE Clean Batch to a Silver Table
(
    movieSilverDF_clean.select(
        "Movie_id",
        "Title",
        "Overview",
        "Tagline",
        "RunTime",
        "Price",
        "Budget",
        "Revenue",
        "CreatedBy",
        "CreatedDate",
        "ReleaseDate",
        "UpdatedBy",
        "UpdatedDate",
        "BackdropUrl",
        "ImdbUrl",
        "PosterUrl",
        "TmdbUrl",
        "movies"
    )
    .write.format("delta")
    .mode("overwrite")
    .save(movieSilverPath)
)

In [0]:
display(dbutils.fs.ls(movieSilverPath))

path name size modificationTime dbfs:/antraBI/ran_wei/movie/Pipline/silver/Movie/_delta_log/ _delta_log/ 0 1691348251000 dbfs:/antraBI/ran_wei/movie/Pipline/silver/Movie/part-00000-02b4bcae-334c-4f2e-af80-f884468dfc5d-c000.snappy.parquet part-00000-02b4bcae-334c-4f2e-af80-f884468dfc5d-c000.snappy.parquet 1577127 1691348253000 dbfs:/antraBI/ran_wei/movie/Pipline/silver/Movie/part-00001-4a06e1e6-29c2-4b17-94d5-440d48d263bb-c000.snappy.parquet part-00001-4a06e1e6-29c2-4b17-94d5-440d48d263bb-c000.snappy.parquet 948860 1691348252000 dbfs:/antraBI/ran_wei/movie/Pipline/silver/Movie/part-00002-56300bf6-49a4-499b-b04f-753defb137ab-c000.snappy.parquet part-00002-56300bf6-49a4-499b-b04f-753defb137ab-c000.snappy.parquet 797477 1691348252000 dbfs:/antraBI/ran_wei/movie/Pipline/silver/Movie/part-00003-386e0b74-bf88-4fc8-8394-2cbd712ed747-c000.snappy.parquet part-00003-386e0b74-bf88-4fc8-8394-2cbd712ed747-c000.snappy.parquet 430171 1691348252000

In [0]:
spark.sql(f"""DROP TABLE IF EXISTS movie_Silver""")

DataFrame[]

In [0]:
spark.sql(
    f"""
    CREATE TABLE movie_Silver
    USING DELTA
    LOCATION "{movieSilverPath}"
    """
)

DataFrame[]

In [0]:
%sql
SELECT * FROM movie_Silver LIMIT 5

Movie_id Title Overview Tagline RunTime Price Budget Revenue CreatedBy CreatedDate ReleaseDate UpdatedBy UpdatedDate BackdropUrl ImdbUrl PosterUrl TmdbUrl movies 1 Inception Cobb, a skilled thief who commits corporate espionage by infiltrating the subconscious of his targets is offered a chance to regain his old life as payment for a task considered to be impossible: "inception", the implantation of another person's idea into a target's subconscious. Your mind is the scene of the crime. 148 9.9 1.6E8 8.25532764E8 null 2021-04-03T16:51:30.1633333 2010-07-15T00:00:00 null null https://image.tmdb.org/t/p/original//s3TBrRGB1iav7gFOCNx3H31MoES.jpg https://www.imdb.com/title/tt1375666 https://image.tmdb.org/t/p/w342//9gk7adHYeDvHkCSEqAvQNLV5Uge.jpg https://www.themoviedb.org/movie/27205 List(https://image.tmdb.org/t/p/original//s3TBrRGB1iav7gFOCNx3H31MoES.jpg, 1.6E8, null, 2021-04-03T16:51:30.1633333, 1, https://www.imdb.com/title/tt1375666, en, Cobb, a skilled thief who commits corporate espionage by infiltrating the subconscious of his targets is offered a chance to regain his old life as payment for a task considered to be impossible: "inception", the implantation of another person's idea into a target's subconscious., https://image.tmdb.org/t/p/w342//9gk7adHYeDvHkCSEqAvQNLV5Uge.jpg, 9.9, 2010-07-15T00:00:00, 8.25532764E8, 148, Your mind is the scene of the crime., Inception, https://www.themoviedb.org/movie/27205, null, null, List(List(1, Adventure), List(6, Action), List(13, Science Fiction))) 2 Interstellar The adventures of a group of explorers who make use of a newly discovered wormhole to surpass the limitations on human space travel and conquer the vast distances involved in an interstellar voyage. Mankind was born on Earth. It was never meant to die here. 169 9.9 1.65E8 6.75120017E8 null 2021-04-03T16:51:30.1633333 2014-11-05T00:00:00 null null https://image.tmdb.org/t/p/original//xJHokMbljvjADYdit5fK5VQsXEG.jpg https://www.imdb.com/title/tt0816692 https://image.tmdb.org/t/p/w342//gEU2QniE6E77NI6lCU6MxlNBvIx.jpg https://www.themoviedb.org/movie/157336 List(https://image.tmdb.org/t/p/original//xJHokMbljvjADYdit5fK5VQsXEG.jpg, 1.65E8, null, 2021-04-03T16:51:30.1633333, 2, https://www.imdb.com/title/tt0816692, en, The adventures of a group of explorers who make use of a newly discovered wormhole to surpass the limitations on human space travel and conquer the vast distances involved in an interstellar voyage., https://image.tmdb.org/t/p/w342//gEU2QniE6E77NI6lCU6MxlNBvIx.jpg, 9.9, 2014-11-05T00:00:00, 6.75120017E8, 169, Mankind was born on Earth. It was never meant to die here., Interstellar, https://www.themoviedb.org/movie/157336, null, null, List(List(1, Adventure), List(4, Drama), List(13, Science Fiction))) 3 The Dark Knight Batman raises the stakes in his war on crime. With the help of Lt. Jim Gordon and District Attorney Harvey Dent, Batman sets out to dismantle the remaining criminal organizations that plague the streets. The partnership proves to be effective, but they soon find themselves prey to a reign of chaos unleashed by a rising criminal mastermind known to the terrified citizens of Gotham as the Joker. Why So Serious? 152 9.9 1.85E8 1.004558444E9 null 2021-04-03T16:51:30.1633333 2008-07-16T00:00:00 null null https://image.tmdb.org/t/p/original//hkBaDkMWbLaf8B1lsWsKX7Ew3Xq.jpg https://www.imdb.com/title/tt0468569 https://image.tmdb.org/t/p/w342//qJ2tW6WMUDux911r6m7haRef0WH.jpg https://www.themoviedb.org/movie/155 List(https://image.tmdb.org/t/p/original//hkBaDkMWbLaf8B1lsWsKX7Ew3Xq.jpg, 1.85E8, null, 2021-04-03T16:51:30.1633333, 3, https://www.imdb.com/title/tt0468569, en, Batman raises the stakes in his war on crime. With the help of Lt. Jim Gordon and District Attorney Harvey Dent, Batman sets out to dismantle the remaining criminal organizations that plague the streets. The partnership proves to be effective, but they soon find themselves prey to a reign of chaos unleashed by a rising criminal mastermind kn

In [0]:
# Update Bronze table
## Update Clean records
bronzeTable = DeltaTable.forPath(spark, bronzePath)
movieSilverAugmented = movieSilverDF_clean.withColumn("status", lit("loaded"))

update_match = "bronze.movies = clean.movies"
update = {"status": "clean.status"}

(
    bronzeTable.alias("bronze")
    .merge(movieSilverAugmented.alias("clean"), update_match)
    .whenMatchedUpdate(set=update)
    .execute()
)

In [0]:
## Update Quarantined records
movieSilverAugmented = movieSilverDF_quarantine.withColumn("status", lit("quarantined"))

update_match = "bronze.movies = quarantine.movies"
update = {"status": "quarantine.status"}

(
    bronzeTable.alias("bronze")
    .merge(movieSilverAugmented.alias("quarantine"), update_match)
    .whenMatchedUpdate(set=update)
    .execute()
)


##3.2 Genre Table

In [0]:
genreSilverAugmentedDF = bronzeDF.select(explode("movies.genres").alias("genres"), "movies")
genreSilverDF = genreSilverAugmentedDF.select(
                                              "genres.id",
                                              "genres.name",
                                              "movies")

In [0]:
genreSilverDF = genreSilverDF.select(
                                      col("id").alias("genre_id"),
                                      col("name").alias("genre_name"),
                                      "movies")

In [0]:
display(genreSilverDF.limit(5))

genre_id genre_name movies 4 Drama List(https://image.tmdb.org/t/p/original//kZGaVeXSkkvrpMYvD97sxHj291k.jpg, 806947.0, null, 2021-04-03T16:51:30.2200000, 323, https://www.imdb.com/title/tt0054215, en, When larcenous real estate clerk Marion Crane goes on the lam with a wad of cash and hopes of starting a new life, she ends up at the notorious Bates Motel, where manager Norman Bates cares for his housebound mother., https://image.tmdb.org/t/p/w342//nR4LD4ZJg2n6LZQpcOrLFdMq0cD.jpg, 9.9, 1960-06-22T00:00:00, 3.2E7, 109, A new—and altogether different—screen excitement!, Psycho, https://www.themoviedb.org/movie/539, null, null, List(List(4, Drama), List(5, Horror), List(10, Thriller))) 5 Horror List(https://image.tmdb.org/t/p/original//kZGaVeXSkkvrpMYvD97sxHj291k.jpg, 806947.0, null, 2021-04-03T16:51:30.2200000, 323, https://www.imdb.com/title/tt0054215, en, When larcenous real estate clerk Marion Crane goes on the lam with a wad of cash and hopes of starting a new life, she ends up at the notorious Bates Motel, where manager Norman Bates cares for his housebound mother., https://image.tmdb.org/t/p/w342//nR4LD4ZJg2n6LZQpcOrLFdMq0cD.jpg, 9.9, 1960-06-22T00:00:00, 3.2E7, 109, A new—and altogether different—screen excitement!, Psycho, https://www.themoviedb.org/movie/539, null, null, List(List(4, Drama), List(5, Horror), List(10, Thriller))) 10 Thriller List(https://image.tmdb.org/t/p/original//kZGaVeXSkkvrpMYvD97sxHj291k.jpg, 806947.0, null, 2021-04-03T16:51:30.2200000, 323, https://www.imdb.com/title/tt0054215, en, When larcenous real estate clerk Marion Crane goes on the lam with a wad of cash and hopes of starting a new life, she ends up at the notorious Bates Motel, where manager Norman Bates cares for his housebound mother., https://image.tmdb.org/t/p/w342//nR4LD4ZJg2n6LZQpcOrLFdMq0cD.jpg, 9.9, 1960-06-22T00:00:00, 3.2E7, 109, A new—and altogether different—screen excitement!, Psycho, https://www.themoviedb.org/movie/539, null, null, List(List(4, Drama), List(5, Horror), List(10, Thriller))) 7 Comedy List(https://image.tmdb.org/t/p/original//hBHxBOGQBTMX3bDmqKoAgniZ9hE.jpg, 0.0, null, 2021-04-03T16:51:30.2233333, 335, https://www.imdb.com/title/tt3846674, en, Lara Jean's love life goes from imaginary to out of control when her secret letters to every boy she's ever fallen for are mysteriously mailed out., https://image.tmdb.org/t/p/w342//hKHZhUbIyUAjcSrqJThFGYIR6kI.jpg, 9.9, 2018-08-16T00:00:00, 0.0, 100, The Letters Are Out., To All the Boys I've Loved Before, https://www.themoviedb.org/movie/466282, null, null, List(List(7, Comedy), List(16, Romance))) 16 Romance List(https://image.tmdb.org/t/p/original//hBHxBOGQBTMX3bDmqKoAgniZ9hE.jpg, 0.0, null, 2021-04-03T16:51:30.2233333, 335, https://www.imdb.com/title/tt3846674, en, Lara Jean's love life goes from imaginary to out of control when her secret letters to every boy she's ever fallen for are mysteriously mailed out., https://image.tmdb.org/t/p/w342//hKHZhUbIyUAjcSrqJThFGYIR6kI.jpg, 9.9, 2018-08-16T00:00:00, 0.0, 100, The Letters Are Out., To All the Boys I've Loved Before, https://www.themoviedb.org/movie/466282, null, null, List(List(7, Comedy), List(16, Romance)))

In [0]:
genreSilverDF.filter("genre_id is not null and genre_name is null").count()

0

All records with valid genre_id have valid genre_name. But if some of the genre name is missing, we should mark it as quarantined first and fix it when updating silver table.

In [0]:
# Join Movie Table
joinDF = movieSilverDF.join(
    genreSilverDF,
    genreSilverDF.movies == movieSilverDF.movies,
)
display(joinDF.limit(5))

Movie_id Title Overview Tagline RunTime Price Budget Revenue CreatedBy CreatedDate ReleaseDate UpdatedBy UpdatedDate BackdropUrl ImdbUrl PosterUrl TmdbUrl movies genre_id genre_name movies 323 Psycho When larcenous real estate clerk Marion Crane goes on the lam with a wad of cash and hopes of starting a new life, she ends up at the notorious Bates Motel, where manager Norman Bates cares for his housebound mother. A new—and altogether different—screen excitement! 109 9.9 806947.0 3.2E7 null 2021-04-03T16:51:30.2200000 1960-06-22T00:00:00 null null https://image.tmdb.org/t/p/original//kZGaVeXSkkvrpMYvD97sxHj291k.jpg https://www.imdb.com/title/tt0054215 https://image.tmdb.org/t/p/w342//nR4LD4ZJg2n6LZQpcOrLFdMq0cD.jpg https://www.themoviedb.org/movie/539 List(https://image.tmdb.org/t/p/original//kZGaVeXSkkvrpMYvD97sxHj291k.jpg, 806947.0, null, 2021-04-03T16:51:30.2200000, 323, https://www.imdb.com/title/tt0054215, en, When larcenous real estate clerk Marion Crane goes on the lam with a wad of cash and hopes of starting a new life, she ends up at the notorious Bates Motel, where manager Norman Bates cares for his housebound mother., https://image.tmdb.org/t/p/w342//nR4LD4ZJg2n6LZQpcOrLFdMq0cD.jpg, 9.9, 1960-06-22T00:00:00, 3.2E7, 109, A new—and altogether different—screen excitement!, Psycho, https://www.themoviedb.org/movie/539, null, null, List(List(4, Drama), List(5, Horror), List(10, Thriller))) 10 Thriller List(https://image.tmdb.org/t/p/original//kZGaVeXSkkvrpMYvD97sxHj291k.jpg, 806947.0, null, 2021-04-03T16:51:30.2200000, 323, https://www.imdb.com/title/tt0054215, en, When larcenous real estate clerk Marion Crane goes on the lam with a wad of cash and hopes of starting a new life, she ends up at the notorious Bates Motel, where manager Norman Bates cares for his housebound mother., https://image.tmdb.org/t/p/w342//nR4LD4ZJg2n6LZQpcOrLFdMq0cD.jpg, 9.9, 1960-06-22T00:00:00, 3.2E7, 109, A new—and altogether different—screen excitement!, Psycho, https://www.themoviedb.org/movie/539, null, null, List(List(4, Drama), List(5, Horror), List(10, Thriller))) 323 Psycho When larcenous real estate clerk Marion Crane goes on the lam with a wad of cash and hopes of starting a new life, she ends up at the notorious Bates Motel, where manager Norman Bates cares for his housebound mother. A new—and altogether different—screen excitement! 109 9.9 806947.0 3.2E7 null 2021-04-03T16:51:30.2200000 1960-06-22T00:00:00 null null https://image.tmdb.org/t/p/original//kZGaVeXSkkvrpMYvD97sxHj291k.jpg https://www.imdb.com/title/tt0054215 https://image.tmdb.org/t/p/w342//nR4LD4ZJg2n6LZQpcOrLFdMq0cD.jpg https://www.themoviedb.org/movie/539 List(https://image.tmdb.org/t/p/original//kZGaVeXSkkvrpMYvD97sxHj291k.jpg, 806947.0, null, 2021-04-03T16:51:30.2200000, 323, https://www.imdb.com/title/tt0054215, en, When larcenous real estate clerk Marion Crane goes on the lam with a wad of cash and hopes of starting a new life, she ends up at the notorious Bates Motel, where manager Norman Bates cares for his housebound mother., https://image.tmdb.org/t/p/w342//nR4LD4ZJg2n6LZQpcOrLFdMq0cD.jpg, 9.9, 1960-06-22T00:00:00, 3.2E7, 109, A new—and altogether different—screen excitement!, Psycho, https://www.themoviedb.org/movie/539, null, null, List(List(4, Drama), List(5, Horror), List(10, Thriller))) 5 Horror List(https://image.tmdb.org/t/p/original//kZGaVeXSkkvrpMYvD97sxHj291k.jpg, 806947.0, null, 2021-04-03T16:51:30.2200000, 323, https://www.imdb.com/title/tt0054215, en, When larcenous real estate clerk Marion Crane goes on the lam with a wad of cash and hopes of starting a new life, she ends up at the notorious Bates Motel, where manager Norman Bates cares for his housebound mother., https://image.tmdb.org/t/p/w342//nR4LD4ZJg2n6LZQpcOrLFdMq0cD.jpg, 9.9, 1960-06-22T00:00:00, 3.2E7, 109, A new—and altogether different—screen excitement!, Psycho, https://www.themoviedb.org/movie/539, null, null, List(List(4, Drama), List(5, Horror), List(10, Thriller))) 323 Psycho When la

In [0]:
# WRITE Batch to a Silver Table
(
    joinDF.select("Movie_id",
                       "Title",
                       "genre_id",
                       "genre_name"
                      )
    .write.format("delta")
    .mode("overwrite")
    .save(genreSilverPath)
)

In [0]:
display(dbutils.fs.ls(genreSilverPath))

path name size modificationTime dbfs:/antraBI/ran_wei/movie/Pipline/silver/Genre/_delta_log/ _delta_log/ 0 1691348583000 dbfs:/antraBI/ran_wei/movie/Pipline/silver/Genre/part-00000-22b8f77c-e2c4-4814-b54f-b8aa0d4fa66b-c000.snappy.parquet part-00000-22b8f77c-e2c4-4814-b54f-b8aa0d4fa66b-c000.snappy.parquet 291215 1691348584000

In [0]:
spark.sql(
    f"""
    CREATE TABLE genre_Silver
    USING DELTA
    LOCATION "{genreSilverPath}"
    """
)

DataFrame[]

In [0]:
%sql
SELECT * FROM genre_Silver LIMIT 5

Movie_id Title genre_id genre_name 323 Psycho 10 Thriller 323 Psycho 5 Horror 323 Psycho 4 Drama 335 To All the Boys I've Loved Before 16 Romance 335 To All the Boys I've Loved Before 7 Comedy

##3.3 OriginalLanguages Table

In [0]:
olSilverArgumentedDF  = bronzeDF.select("movies.Id",
                                "movies.Title",
                                "movies.OriginalLanguage",
                                "movies"
                               )

In [0]:
olSilverDF = olSilverArgumentedDF.select(
                                          col("Id").alias("Movie_id"),
                                          col("Title"),
                                          "OriginalLanguage",
                                          "movies"
                                        )
display(olSilverDF)

Movie_id Title OriginalLanguage movies 323 Psycho en List(https://image.tmdb.org/t/p/original//kZGaVeXSkkvrpMYvD97sxHj291k.jpg, 806947.0, null, 2021-04-03T16:51:30.2200000, 323, https://www.imdb.com/title/tt0054215, en, When larcenous real estate clerk Marion Crane goes on the lam with a wad of cash and hopes of starting a new life, she ends up at the notorious Bates Motel, where manager Norman Bates cares for his housebound mother., https://image.tmdb.org/t/p/w342//nR4LD4ZJg2n6LZQpcOrLFdMq0cD.jpg, 9.9, 1960-06-22T00:00:00, 3.2E7, 109, A new—and altogether different—screen excitement!, Psycho, https://www.themoviedb.org/movie/539, null, null, List(List(4, Drama), List(5, Horror), List(10, Thriller))) 335 To All the Boys I've Loved Before en List(https://image.tmdb.org/t/p/original//hBHxBOGQBTMX3bDmqKoAgniZ9hE.jpg, 0.0, null, 2021-04-03T16:51:30.2233333, 335, https://www.imdb.com/title/tt3846674, en, Lara Jean's love life goes from imaginary to out of control when her secret letters to every boy she's ever fallen for are mysteriously mailed out., https://image.tmdb.org/t/p/w342//hKHZhUbIyUAjcSrqJThFGYIR6kI.jpg, 9.9, 2018-08-16T00:00:00, 0.0, 100, The Letters Are Out., To All the Boys I've Loved Before, https://www.themoviedb.org/movie/466282, null, null, List(List(7, Comedy), List(16, Romance))) 429 The Kissing Booth en List(https://image.tmdb.org/t/p/original//itiz2OBK4ns6XT0ufXtusojmMt9.jpg, 0.0, null, 2021-04-03T16:51:30.2366667, 429, https://www.imdb.com/title/tt3799232, en, When teenager Elle's first kiss leads to a forbidden romance with the hottest boy in high school, she risks her relationship with her best friend., https://image.tmdb.org/t/p/w342//7Dktk2ST6aL8h9Oe5rpk903VLhx.jpg, 9.9, 2018-05-11T00:00:00, 0.0, 105, She can tell her best friend anything, except this one thing, The Kissing Booth, https://www.themoviedb.org/movie/454983, null, null, List(List(7, Comedy), List(16, Romance))) 494 12 Angry Men en List(https://image.tmdb.org/t/p/original//qqHQsStV6exghCM7zbObuYBiYxw.jpg, 350000.0, null, 2021-04-03T16:51:30.2466667, 494, https://www.imdb.com/title/tt0050083, en, The defense and the prosecution have rested and the jury is filing into the jury room to decide if a young Spanish-American is guilty or innocent of murdering his father. What begins as an open and shut case soon becomes a mini-drama of each of the jurors' prejudices and preconceptions about the trial, the accused, and each other., https://image.tmdb.org/t/p/w342//wh0f80G6GZvYBNiYmvqFngt3IYq.jpg, 9.9, 1957-04-10T00:00:00, 1000000.0, 97, Life is in their hands. Death is on their minds., 12 Angry Men, https://www.themoviedb.org/movie/389, null, null, List(List(4, Drama))) 560 Love, Rosie en List(https://image.tmdb.org/t/p/original//unJJDP1dE1cfLJojUKVOHJ7zKJe.jpg, 0.0, null, 2021-04-03T16:51:30.2566667, 560, https://www.imdb.com/title/tt1638002, en, Since the moment they met at age 5, Rosie and Alex have been best friends, facing the highs and lows of growing up side by side. A fleeting shared moment, one missed opportunity, and the decisions that follow send their lives in completely different directions. As each navigates the complexities of life, love, and everything in between, they always find their way back to each other - but is it just friendship, or something more?, https://image.tmdb.org/t/p/w342//rpD0t7DhzJVadnzgxSYrqljQTL2.jpg, 9.9, 2014-10-16T00:00:00, 4439431.0, 102, Right Love. Wrong Time., Love, Rosie, https://www.themoviedb.org/movie/200727, null, null, List(List(7, Comedy), List(16, Romance))) 717 Bambi en List(https://image.tmdb.org/t/p/original//fgIeKLbmPLof5cb88Wod0CWhWTE.jpg, 858000.0, null, 2021-04-03T16:51:30.2800000, 717, https://www.imdb.com/title/tt0034492, en, Bambi's tale unfolds from season to season as the young prince of the forest learns about life, love, and friends., https://image.tmdb.org/t/p/w342//wV9e2y4myJ4KMFsyFfWYcUOawyK.jpg, 9.9, 1942-08-14T00:00:00, 2.6744715E8, 65, A great love story., Bambi, https://www.themov

In [0]:
olSilverDF.count()

9995

In [0]:
# WRITE Batch to a Silver Table
(
    olSilverDF.select("Movie_id",
                       "Title",
                       "OriginalLanguage",
                       "movies"
                      )
    .write.format("delta")
    .mode("overwrite")
    .save(olSilverPath)
)

In [0]:
display(dbutils.fs.ls(olSilverPath))

path name size modificationTime dbfs:/antraBI/ran_wei/movie/Pipline/silver/OriginalLanguages/_delta_log/ _delta_log/ 0 1691348825000 dbfs:/antraBI/ran_wei/movie/Pipline/silver/OriginalLanguages/part-00000-2c87094c-7fcf-4d68-9381-e35a00a93ea7-c000.snappy.parquet part-00000-2c87094c-7fcf-4d68-9381-e35a00a93ea7-c000.snappy.parquet 3458607 1691348826000

In [0]:
spark.sql(
    f"""
    CREATE TABLE original_language_Silver
    USING DELTA
    LOCATION "{olSilverPath}"
    """
)

DataFrame[]

In [0]:
%sql
SELECT * FROM original_language_Silver LIMIT 5

Movie_id Title OriginalLanguage movies 323 Psycho en List(https://image.tmdb.org/t/p/original//kZGaVeXSkkvrpMYvD97sxHj291k.jpg, 806947.0, null, 2021-04-03T16:51:30.2200000, 323, https://www.imdb.com/title/tt0054215, en, When larcenous real estate clerk Marion Crane goes on the lam with a wad of cash and hopes of starting a new life, she ends up at the notorious Bates Motel, where manager Norman Bates cares for his housebound mother., https://image.tmdb.org/t/p/w342//nR4LD4ZJg2n6LZQpcOrLFdMq0cD.jpg, 9.9, 1960-06-22T00:00:00, 3.2E7, 109, A new—and altogether different—screen excitement!, Psycho, https://www.themoviedb.org/movie/539, null, null, List(List(4, Drama), List(5, Horror), List(10, Thriller))) 335 To All the Boys I've Loved Before en List(https://image.tmdb.org/t/p/original//hBHxBOGQBTMX3bDmqKoAgniZ9hE.jpg, 0.0, null, 2021-04-03T16:51:30.2233333, 335, https://www.imdb.com/title/tt3846674, en, Lara Jean's love life goes from imaginary to out of control when her secret letters to every boy she's ever fallen for are mysteriously mailed out., https://image.tmdb.org/t/p/w342//hKHZhUbIyUAjcSrqJThFGYIR6kI.jpg, 9.9, 2018-08-16T00:00:00, 0.0, 100, The Letters Are Out., To All the Boys I've Loved Before, https://www.themoviedb.org/movie/466282, null, null, List(List(7, Comedy), List(16, Romance))) 429 The Kissing Booth en List(https://image.tmdb.org/t/p/original//itiz2OBK4ns6XT0ufXtusojmMt9.jpg, 0.0, null, 2021-04-03T16:51:30.2366667, 429, https://www.imdb.com/title/tt3799232, en, When teenager Elle's first kiss leads to a forbidden romance with the hottest boy in high school, she risks her relationship with her best friend., https://image.tmdb.org/t/p/w342//7Dktk2ST6aL8h9Oe5rpk903VLhx.jpg, 9.9, 2018-05-11T00:00:00, 0.0, 105, She can tell her best friend anything, except this one thing, The Kissing Booth, https://www.themoviedb.org/movie/454983, null, null, List(List(7, Comedy), List(16, Romance))) 494 12 Angry Men en List(https://image.tmdb.org/t/p/original//qqHQsStV6exghCM7zbObuYBiYxw.jpg, 350000.0, null, 2021-04-03T16:51:30.2466667, 494, https://www.imdb.com/title/tt0050083, en, The defense and the prosecution have rested and the jury is filing into the jury room to decide if a young Spanish-American is guilty or innocent of murdering his father. What begins as an open and shut case soon becomes a mini-drama of each of the jurors' prejudices and preconceptions about the trial, the accused, and each other., https://image.tmdb.org/t/p/w342//wh0f80G6GZvYBNiYmvqFngt3IYq.jpg, 9.9, 1957-04-10T00:00:00, 1000000.0, 97, Life is in their hands. Death is on their minds., 12 Angry Men, https://www.themoviedb.org/movie/389, null, null, List(List(4, Drama))) 560 Love, Rosie en List(https://image.tmdb.org/t/p/original//unJJDP1dE1cfLJojUKVOHJ7zKJe.jpg, 0.0, null, 2021-04-03T16:51:30.2566667, 560, https://www.imdb.com/title/tt1638002, en, Since the moment they met at age 5, Rosie and Alex have been best friends, facing the highs and lows of growing up side by side. A fleeting shared moment, one missed opportunity, and the decisions that follow send their lives in completely different directions. As each navigates the complexities of life, love, and everything in between, they always find their way back to each other - but is it just friendship, or something more?, https://image.tmdb.org/t/p/w342//rpD0t7DhzJVadnzgxSYrqljQTL2.jpg, 9.9, 2014-10-16T00:00:00, 4439431.0, 102, Right Love. Wrong Time., Love, Rosie, https://www.themoviedb.org/movie/200727, null, null, List(List(7, Comedy), List(16, Romance)))

#4. Silver Update (Movie)

In [0]:
display(movieSilverDF_quarantine.limit(5))

Movie_id Title Overview Tagline RunTime Price Budget Revenue CreatedBy CreatedDate ReleaseDate UpdatedBy UpdatedDate BackdropUrl ImdbUrl PosterUrl TmdbUrl movies 323 Psycho When larcenous real estate clerk Marion Crane goes on the lam with a wad of cash and hopes of starting a new life, she ends up at the notorious Bates Motel, where manager Norman Bates cares for his housebound mother. A new—and altogether different—screen excitement! 109 9.9 806947.0 3.2E7 null 2021-04-03T16:51:30.2200000 1960-06-22T00:00:00 null null https://image.tmdb.org/t/p/original//kZGaVeXSkkvrpMYvD97sxHj291k.jpg https://www.imdb.com/title/tt0054215 https://image.tmdb.org/t/p/w342//nR4LD4ZJg2n6LZQpcOrLFdMq0cD.jpg https://www.themoviedb.org/movie/539 List(https://image.tmdb.org/t/p/original//kZGaVeXSkkvrpMYvD97sxHj291k.jpg, 806947.0, null, 2021-04-03T16:51:30.2200000, 323, https://www.imdb.com/title/tt0054215, en, When larcenous real estate clerk Marion Crane goes on the lam with a wad of cash and hopes of starting a new life, she ends up at the notorious Bates Motel, where manager Norman Bates cares for his housebound mother., https://image.tmdb.org/t/p/w342//nR4LD4ZJg2n6LZQpcOrLFdMq0cD.jpg, 9.9, 1960-06-22T00:00:00, 3.2E7, 109, A new—and altogether different—screen excitement!, Psycho, https://www.themoviedb.org/movie/539, null, null, List(List(4, Drama), List(5, Horror), List(10, Thriller))) 335 To All the Boys I've Loved Before Lara Jean's love life goes from imaginary to out of control when her secret letters to every boy she's ever fallen for are mysteriously mailed out. The Letters Are Out. 100 9.9 0.0 0.0 null 2021-04-03T16:51:30.2233333 2018-08-16T00:00:00 null null https://image.tmdb.org/t/p/original//hBHxBOGQBTMX3bDmqKoAgniZ9hE.jpg https://www.imdb.com/title/tt3846674 https://image.tmdb.org/t/p/w342//hKHZhUbIyUAjcSrqJThFGYIR6kI.jpg https://www.themoviedb.org/movie/466282 List(https://image.tmdb.org/t/p/original//hBHxBOGQBTMX3bDmqKoAgniZ9hE.jpg, 0.0, null, 2021-04-03T16:51:30.2233333, 335, https://www.imdb.com/title/tt3846674, en, Lara Jean's love life goes from imaginary to out of control when her secret letters to every boy she's ever fallen for are mysteriously mailed out., https://image.tmdb.org/t/p/w342//hKHZhUbIyUAjcSrqJThFGYIR6kI.jpg, 9.9, 2018-08-16T00:00:00, 0.0, 100, The Letters Are Out., To All the Boys I've Loved Before, https://www.themoviedb.org/movie/466282, null, null, List(List(7, Comedy), List(16, Romance))) 429 The Kissing Booth When teenager Elle's first kiss leads to a forbidden romance with the hottest boy in high school, she risks her relationship with her best friend. She can tell her best friend anything, except this one thing 105 9.9 0.0 0.0 null 2021-04-03T16:51:30.2366667 2018-05-11T00:00:00 null null https://image.tmdb.org/t/p/original//itiz2OBK4ns6XT0ufXtusojmMt9.jpg https://www.imdb.com/title/tt3799232 https://image.tmdb.org/t/p/w342//7Dktk2ST6aL8h9Oe5rpk903VLhx.jpg https://www.themoviedb.org/movie/454983 List(https://image.tmdb.org/t/p/original//itiz2OBK4ns6XT0ufXtusojmMt9.jpg, 0.0, null, 2021-04-03T16:51:30.2366667, 429, https://www.imdb.com/title/tt3799232, en, When teenager Elle's first kiss leads to a forbidden romance with the hottest boy in high school, she risks her relationship with her best friend., https://image.tmdb.org/t/p/w342//7Dktk2ST6aL8h9Oe5rpk903VLhx.jpg, 9.9, 2018-05-11T00:00:00, 0.0, 105, She can tell her best friend anything, except this one thing, The Kissing Booth, https://www.themoviedb.org/movie/454983, null, null, List(List(7, Comedy), List(16, Romance))) 494 12 Angry Men The defense and the prosecution have rested and the jury is filing into the jury room to decide if a young Spanish-American is guilty or innocent of murdering his father. What begins as an open and shut case soon becomes a mini-drama of each of the jurors' prejudices and preconceptions about the trial, the accused, and each other. Life is in their hands. Death is on their minds. 97 9.9 350000.0 1000000.0 null 2021-04-0

In [0]:
# replace the budget<1 million with 1 million
moviesUpdatedDF = movieSilverDF_quarantine.withColumn("Budget", lit(1000000))

moviesConcatenatedDF = moviesUpdatedDF.union(movieSilverDF_clean)

In [0]:
moviesConcatenatedDF.count()

9995

In [0]:
moviesConcatenatedDF.filter("Budget<1000000").count()

0

In [0]:
# WRITE Clean Batch to a Silver Update Table
(
    moviesConcatenatedDF.select(
        "Movie_id",
        "Title",
        "Overview",
        "Tagline",
        "RunTime",
        "Price",
        "Budget",
        "Revenue",
        "CreatedBy",
        "CreatedDate",
        "ReleaseDate",
        "UpdatedBy",
        "UpdatedDate",
        "BackdropUrl",
        "ImdbUrl",
        "PosterUrl",
        "TmdbUrl",
        "Movies"
    )
    .write.format("delta")
    .mode("overwrite")
    .save(movieSilverUpdatePath)
)

In [0]:
display(dbutils.fs.ls(movieSilverUpdatePath))

path name size modificationTime dbfs:/antraBI/ran_wei/movie/Pipline/silverUpdate/Movie/_delta_log/ _delta_log/ 0 1691348989000 dbfs:/antraBI/ran_wei/movie/Pipline/silverUpdate/Movie/part-00000-6a6d7eab-e162-43f8-85b1-46ef10f23ae1-c000.snappy.parquet part-00000-6a6d7eab-e162-43f8-85b1-46ef10f23ae1-c000.snappy.parquet 2863210 1691348991000 dbfs:/antraBI/ran_wei/movie/Pipline/silverUpdate/Movie/part-00001-aa7df1a0-ec05-4768-b43f-1a4878486517-c000.snappy.parquet part-00001-aa7df1a0-ec05-4768-b43f-1a4878486517-c000.snappy.parquet 3681863 1691348991000

In [0]:
spark.sql(
    f"""
    CREATE TABLE movie_Silver_Update
    USING DELTA
    LOCATION "{movieSilverUpdatePath}"
    """
)

DataFrame[]

In [0]:
%sql
SELECT * FROM movie_Silver_Update LIMIT 5

Movie_id Title Overview Tagline RunTime Price Budget Revenue CreatedBy CreatedDate ReleaseDate UpdatedBy UpdatedDate BackdropUrl ImdbUrl PosterUrl TmdbUrl Movies 323 Psycho When larcenous real estate clerk Marion Crane goes on the lam with a wad of cash and hopes of starting a new life, she ends up at the notorious Bates Motel, where manager Norman Bates cares for his housebound mother. A new—and altogether different—screen excitement! 109 9.9 1000000.0 3.2E7 null 2021-04-03T16:51:30.2200000 1960-06-22T00:00:00 null null https://image.tmdb.org/t/p/original//kZGaVeXSkkvrpMYvD97sxHj291k.jpg https://www.imdb.com/title/tt0054215 https://image.tmdb.org/t/p/w342//nR4LD4ZJg2n6LZQpcOrLFdMq0cD.jpg https://www.themoviedb.org/movie/539 List(https://image.tmdb.org/t/p/original//kZGaVeXSkkvrpMYvD97sxHj291k.jpg, 806947.0, null, 2021-04-03T16:51:30.2200000, 323, https://www.imdb.com/title/tt0054215, en, When larcenous real estate clerk Marion Crane goes on the lam with a wad of cash and hopes of starting a new life, she ends up at the notorious Bates Motel, where manager Norman Bates cares for his housebound mother., https://image.tmdb.org/t/p/w342//nR4LD4ZJg2n6LZQpcOrLFdMq0cD.jpg, 9.9, 1960-06-22T00:00:00, 3.2E7, 109, A new—and altogether different—screen excitement!, Psycho, https://www.themoviedb.org/movie/539, null, null, List(List(4, Drama), List(5, Horror), List(10, Thriller))) 335 To All the Boys I've Loved Before Lara Jean's love life goes from imaginary to out of control when her secret letters to every boy she's ever fallen for are mysteriously mailed out. The Letters Are Out. 100 9.9 1000000.0 0.0 null 2021-04-03T16:51:30.2233333 2018-08-16T00:00:00 null null https://image.tmdb.org/t/p/original//hBHxBOGQBTMX3bDmqKoAgniZ9hE.jpg https://www.imdb.com/title/tt3846674 https://image.tmdb.org/t/p/w342//hKHZhUbIyUAjcSrqJThFGYIR6kI.jpg https://www.themoviedb.org/movie/466282 List(https://image.tmdb.org/t/p/original//hBHxBOGQBTMX3bDmqKoAgniZ9hE.jpg, 0.0, null, 2021-04-03T16:51:30.2233333, 335, https://www.imdb.com/title/tt3846674, en, Lara Jean's love life goes from imaginary to out of control when her secret letters to every boy she's ever fallen for are mysteriously mailed out., https://image.tmdb.org/t/p/w342//hKHZhUbIyUAjcSrqJThFGYIR6kI.jpg, 9.9, 2018-08-16T00:00:00, 0.0, 100, The Letters Are Out., To All the Boys I've Loved Before, https://www.themoviedb.org/movie/466282, null, null, List(List(7, Comedy), List(16, Romance))) 429 The Kissing Booth When teenager Elle's first kiss leads to a forbidden romance with the hottest boy in high school, she risks her relationship with her best friend. She can tell her best friend anything, except this one thing 105 9.9 1000000.0 0.0 null 2021-04-03T16:51:30.2366667 2018-05-11T00:00:00 null null https://image.tmdb.org/t/p/original//itiz2OBK4ns6XT0ufXtusojmMt9.jpg https://www.imdb.com/title/tt3799232 https://image.tmdb.org/t/p/w342//7Dktk2ST6aL8h9Oe5rpk903VLhx.jpg https://www.themoviedb.org/movie/454983 List(https://image.tmdb.org/t/p/original//itiz2OBK4ns6XT0ufXtusojmMt9.jpg, 0.0, null, 2021-04-03T16:51:30.2366667, 429, https://www.imdb.com/title/tt3799232, en, When teenager Elle's first kiss leads to a forbidden romance with the hottest boy in high school, she risks her relationship with her best friend., https://image.tmdb.org/t/p/w342//7Dktk2ST6aL8h9Oe5rpk903VLhx.jpg, 9.9, 2018-05-11T00:00:00, 0.0, 105, She can tell her best friend anything, except this one thing, The Kissing Booth, https://www.themoviedb.org/movie/454983, null, null, List(List(7, Comedy), List(16, Romance))) 494 12 Angry Men The defense and the prosecution have rested and the jury is filing into the jury room to decide if a young Spanish-American is guilty or innocent of murdering his father. What begins as an open and shut case soon becomes a mini-drama of each of the jurors' prejudices and preconceptions about the trial, the accused, and each other. Life is in their hands. Death is on their minds. 97 9.9 1000000.0 1000000.0 

In [0]:
# Update Bronze table
bronzeTable = DeltaTable.forPath(spark, bronzePath)
movieSilverAugmented = moviesConcatenatedDF.withColumn("status", lit("loaded"))

update_match = "bronze.movies = clean.movies"
update = {"status": "clean.status"}

(
    bronzeTable.alias("bronze")
    .merge(movieSilverAugmented.alias("clean"), update_match)
    .whenMatchedUpdate(set=update)
    .execute()
)

In [0]:
bronzeDF = (spark.read
         .format("delta")
         .load(bronzePath))

In [0]:
bronzeDF.count()

9995

In [0]:
bronzeDF.filter("status='loaded'").count()

9995